In [27]:
import spacy_dbpedia_spotlight
import spacy
import pandas as pd
import time
import requests
from difflib import SequenceMatcher
from tqdm import tqdm
import csv
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import train_test_split

In [34]:
#Read TextCorpus for Annotation
df = pd.read_pickle('data/textCorpusCleanedV1.0')
df.shape

(3210, 2)

In [35]:
#df = df.head(25).copy()
#df.shape

In [36]:
#spotlight = spacy_dbpedia_spotlight.create('en') # superseded from old gpu server spacy_dbpedia_spotlight.load('en') 

spotlight = spacy.blank('en')
spotlight.add_pipe('dbpedia_spotlight', config={'confidence': 0.25})

#sentencizer = spacy.load('en_core_web_sm')

In [37]:
def clean_text(text):
    cleaned_text = text.replace(',', '')
    cleaned_text = text.replace('"', '')
    cleaned_text = cleaned_text.replace('.', ' ')
    cleaned_text = cleaned_text.replace('(', '')
    cleaned_text = cleaned_text.replace(')', '')
    return cleaned_text.strip()

In [38]:
#Split sentences to rows to be able to distinguish sentences with multiple or no entities.
def split_sents(text):
    entities =[]
    #Due to long texts, we gotta split them for the requests..
    #doc = sentencizer(text)
    #sentences = [clean_text(sent.text) for sent in doc.sents]
    
    sentences = text.split('.')
    sentences = [sent for sent in sentences]
    
    for i, sent in enumerate(sentences):
        sentences[i] = sentences[i].replace(',', '')
        sentences[i] = sentences[i].replace(',', '')
        sentences[i] = sentences[i].replace('"', '')
        sentences[i] = sentences[i].replace('.', ' ')
        sentences[i] = sentences[i].replace('(', '')
        sentences[i] = sentences[i].replace(')', '')
    
    return sentences

df["text"] = df["text"].apply(lambda row: split_sents(row) )
df = df.explode("text")
df.reset_index(inplace=True)

In [39]:
df.text[0]

'gamma-Hydroxybutyric acid or -Hydroxybutyric acid GHB also known as 4-hydroxybutanoic acid is a naturally occurring neurotransmitter and a psychoactive drug'

In [7]:
#Annotation method
def annotate_text(text):
    entities =[]
    #Due to long texts, we gotta split them for the requests..
    #doc = sentencizer(text)
    #sentences = [sent.string.strip() for sent in doc.sents]
    
    #for sentence in sentences:
    try:
        doc2 = spotlight(text)
        entities.extend([(ent.text, ent.kb_id_) for ent in doc2.ents])
    except Exception as e:
        print('Error ', e, ' at ', text) #sentence)
    #entities =  [(ent.text, ent.label_, ent.kb_id_) for ent in doc.ents]
    
    
    return list(dict.fromkeys(entities)) #Return only unique entries..



In [8]:
#%%time
tqdm.pandas()

df['entities'] = df['text'].progress_apply(lambda text: annotate_text(text))

  0%|          | 32/202476 [00:03<5:23:59, 10.41it/s]

24 37 {'@URI': 'http://dbpedia.org/resource/Butyrolactone', '@support': '11', '@types': '', '@surfaceForm': 'butyrolactone', '@offset': '24', '@similarityScore': '0.9999999251796537', '@percentageOfSecondRank': '0.0'}


  0%|          | 40/202476 [00:04<5:21:49, 10.48it/s]

Error  [E1010] Unable to set entity information for token 7 which is included in more than one span in entities, blocked, missing or outside.  at  A 2006 report commissioned by a UK parliamentary committee found the use of GHB to be less dangerous than tobacco and alcohol in physical harm, dependence and social harms


  0%|          | 65/202476 [00:06<5:17:16, 10.63it/s]

...

100%|█████████▉| 202472/202476 [6:06:11<00:00,  9.26it/s]

Error  [E1010] Unable to set entity information for token 121 which is included in more than one span in entities, blocked, missing or outside.  at  Paperback: App 200 pages -  Publisher: The Beckley Foundation Press and Oxford University Press June 2010 ISBN 978-0-19-958982-1  Hoffmanns Elixir: LSD and the new Eleusis - Talks & Essays by Albert Hofmann and othersEdited by Amanda Feilding -  Publisher: Beckley Foundation Press 2010 ISBN 978-0-9548054-9-4  Non-Invasive Evaluation of Human Brain Fluid Dynamics and Skull Biomechanics in Relation to Cognitive FunctioningAuthors: Yuri Moskalenko, Amanda Feilding and Peter Halvorson -  Publisher: Beckley Foundation Press 2010 ISBN 978-1-907072-01-7 Drugs and the Brain, Magdalen College, Oxford, 2002


100%|██████████| 202476/202476 [6:06:11<00:00,  9.52it/s]

Error  [E1010] Unable to set entity information for token 35 which is included in more than one span in entities, blocked, missing or outside.  at  A three-day seminar including the Beckley/Foresight Seminar, reviewing the Foresight Report; the meeting of the International Consortium of NGOs, and the meeting of the International Network of Drug Policy Analysis, renamed International Society for the Study of Drug Policy ISSDP
197 204 {'@URI': 'http://dbpedia.org/resource/Control_engineering', '@support': '395', '@types': '', '@surfaceForm': 'Control', '@offset': '197', '@similarityScore': '0.9337562374664464', '@percentageOfSecondRank': '0.029781743511666084'}


100%|██████████| 202476/202476 [6:06:11<00:00,  9.22it/s]


In [9]:
#Get a list of all entities contained
all_entity_list = df.entities.sum()
#Remove duplicates
unique_entities = list(dict.fromkeys(all_entity_list))

print(len(unique_entities), ' entities need to be matched')

135750  entities need to be matched


In [10]:
unique_entities

[('gamma-Hydroxybutyric acid',
  'http://dbpedia.org/resource/Gamma-Hydroxybutyric_acid'),
 ('acid', 'http://dbpedia.org/resource/Lysergic_acid_diethylamide'),
 ('GHB', 'http://dbpedia.org/resource/Gamma-Hydroxybutyric_acid'),
 ('naturally', 'http://dbpedia.org/resource/Natural_product'),
 ('neurotransmitter', 'http://dbpedia.org/resource/Neurotransmitter'),
 ('psychoactive drug', 'http://dbpedia.org/resource/Psychoactive_drug'),
 ('It', 'http://dbpedia.org/resource/Schizophrenia'),
 ('GABA', 'http://dbpedia.org/resource/Gamma-Aminobutyric_acid'),
 ('glutamate', 'http://dbpedia.org/resource/Glutamic_acid'),
 ('glycine', 'http://dbpedia.org/resource/Glycine'),
 ('brain', 'http://dbpedia.org/resource/Brain'),
 ('areas', "http://dbpedia.org/resource/Broca's_area"),
 ('acts', 'http://dbpedia.org/resource/Act_of_Parliament'),
 ('GHB receptor', 'http://dbpedia.org/resource/GHB_receptor'),
 ('weak', 'http://dbpedia.org/resource/Weak_interaction'),
 ('agonist', 'http://dbpedia.org/resource/Ago

In [11]:
#Test Setting with only 10 entities
#unique_entities = unique_entities[:500]

In [12]:
%%time

illegalDrugIndicators = [#'dbp:legalAu', # 'dbp:legalCa', 'dbp:legalDe', 'dbp:legalNz', 
                         #'dbp:legalUk',
    'dbp:legalUn', 'dbp:legalUs']

list_of_drugs = []
url = 'http://dbpedia.org/sparql'

#for ent_tuple in unique_entities:
for ent_tuple in tqdm(unique_entities):
    
    for ind in illegalDrugIndicators:
        query = """
                select * where {
                <""" + ent_tuple[1] + "> " + ind + " " + "?c" + """ }
                LIMIT 100
                """
        try:
            r = requests.get(url, params = {'format': 'json', 'query': query})
            data = r.json()

            if len(data['results']['bindings']) > 0:
                list_of_drugs.append(ent_tuple)
                break
        except Exception as e:
            print('Error ', e, ' at ', ent_tuple, ' and relation ', ind)
        
        

  6%|▌         | 8041/135750 [48:14<12:37:57,  2.81it/s]

Error  HTTPConnectionPool(host='dbpedia.org', port=80): Max retries exceeded with url: /sparql?format=json&query=%0A++++++++++++++++select+%2A+where+%7B%0A++++++++++++++++%3Chttp%3A%2F%2Fdbpedia.org%2Fresource%2FAbiogenesis%3E+dbp%3AlegalUn+%3Fc+%7D%0A++++++++++++++++LIMIT+100%0A++++++++++++++++ (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7fad5c145b00>: Failed to establish a new connection: [Errno 101] Network is unreachable',))  at  ('The origin', 'http://dbpedia.org/resource/Abiogenesis')  and relation  dbp:legalUn


  6%|▌         | 8042/135750 [51:02<1794:10:40, 50.58s/it]

Error  ('Connection aborted.', OSError(0, 'Error'))  at  ('The origin', 'http://dbpedia.org/resource/Abiogenesis')  and relation  dbp:legalUs


 10%|▉         | 13153/135750 [1:21:41<19:00:06,  1.79it/s]

...

Error  Expecting value: line 1 column 1 (char 0)  at  ('Margarete Himmler', 'http://dbpedia.org/resource/Margarete_Himmler')  and relation  dbp:legalUn


 99%|█████████▉| 134324/135750 [13:20:13<07:58,  2.98it/s]

Error  Expecting value: line 1 column 1 (char 0)  at  ('Himmler', 'http://dbpedia.org/resource/Heinrich_Himmler')  and relation  dbp:legalUn
Error  Expecting value: line 1 column 1 (char 0)  at  ('Himmler', 'http://dbpedia.org/resource/Heinrich_Himmler')  and relation  dbp:legalUs


100%|██████████| 135750/135750 [13:28:36<00:00,  2.80it/s]

CPU times: user 2h 12min 45s, sys: 4min 37s, total: 2h 17min 23s
Wall time: 13h 28min 36s


In [13]:
#The resource link is unique and needs to be the identifier. Otherwise different writings linked to the known drug might be ignored..
drug_dict = {y:x for x,y in dict(list_of_drugs).items()}
drug_dict


{'http://dbpedia.org/resource/Gamma-Hydroxybutyric_acid': '4-Hydroxybutanoic acid',
 'http://dbpedia.org/resource/Lysergic_acid_diethylamide': 'flashback',
 'http://dbpedia.org/resource/Sodium_oxybate': 'Sodium oxybate',
 'http://dbpedia.org/resource/MDMA': 'xtc',
 'http://dbpedia.org/resource/Diazepam': 'valium',
 'http://dbpedia.org/resource/Baclofen': 'baclofen',
 'http://dbpedia.org/resource/Lorazepam': 'Ativan',
 'http://dbpedia.org/resource/Phenibut': 'Phenibut',
 'http://dbpedia.org/resource/Naloxone': 'suboxone',
 'http://dbpedia.org/resource/Naltrexone': 'Mysimba',
 'http://dbpedia.org/resource/Chlordiazepoxide': 'Limbitrol',
 'http://dbpedia.org/resource/Pregabalin': 'Pregabalin',
 'http://dbpedia.org/resource/Alprazolam': 'xanax',
 'http://dbpedia.org/resource/Bromazepam': 'Lexotanil',
 'http://dbpedia.org/resource/Nitrazepam': 'Mogadon',
 'http://dbpedia.org/resource/Clonazepam': 'klonopin',
 'http://dbpedia.org/resource/Midazolam': 'Dormicum',
 'http://dbpedia.org/resource

In [14]:
def label_drugs_in_text(entity_list, text, lookup_dict):
    final_text = text
    for candidate in entity_list:
        if candidate[1] in lookup_dict:
            final_text = final_text.replace(candidate[0], '<DRUG> '+candidate[0]+ ' </DRUG>')
    return final_text

def create_drug_label_list(entity_list, text, lookup_dict):
    labels = []
    for candidate in entity_list:
        if candidate[1] in lookup_dict:
            labels.append((candidate[0], 'Drug'))
    return labels
            

In [15]:
#df["newText"] = df.apply(lambda row: create_drug_label_list(row['entities'], row['text'], drug_dict2), axis=1)
df["labels"] = df.apply(lambda row: create_drug_label_list(row['entities'], row['text'], drug_dict), axis=1)

In [16]:
#Store raw
df.to_pickle('data/raw_annotated_DF_V1.2')

In [17]:
#Remove sentences without Drug label
index_to_del = df[ df['labels'].map(lambda d: len(d)) <= 0 ].index
df.drop(index_to_del, inplace=True)

In [18]:
#Store reduced Sentence set as Domain Text corpora
np.savetxt('data/reducedTextCorpusV1.2.txt', df["text"].values, fmt = "%s")

In [19]:
#Convert to BIO-NER task format
# Credits to Akash Chauhan - chauhanakash23.github.io

def matcher(string, pattern):
    '''
    Return the start and end index of any pattern present in the text.
    '''
    match_list = []
    pattern = pattern.strip()
    seqMatch = SequenceMatcher(None, string, pattern, autojunk=False)
    match = seqMatch.find_longest_match(0, len(string), 0, len(pattern))
    if (match.size == len(pattern)):
        start = match.a
        end = match.a + match.size
        match_tup = (start, end)
        string = string.replace(pattern, "X" * len(pattern), 1)
        match_list.append(match_tup)
        
    return match_list, string

def mark_sentence(s, match_list):
    '''
    Marks all the entities in the sentence as per the BIO scheme. 
    '''
    word_dict = {}
    for word in s.split():
        word_dict[word] = 'O'
        
    for start, end, e_type in match_list:
        temp_str = s[start:end]
        tmp_list = temp_str.split()
        if len(tmp_list) > 1:
            word_dict[tmp_list[0]] = 'B-' + e_type
            for w in tmp_list[1:]:
                word_dict[w] = 'I-' + e_type
        else:
            word_dict[temp_str] = 'B-' + e_type
    return word_dict

''' NOT NECESSARY SINCE CLEANING IS DONE ELSEWHERE
def clean(text):
    
    #Just a helper fuction to add a space before the punctuations for better tokenization
    filters = ["!", "#", "$", "%", "&", "(", ")", "/", "*", ".", ":", ";", "<", "=", ">", "?", "@", "[",
               "\\", "]", "_", "`", "{", "}", "~", "'"]
    for i in text:
        if i in filters:
            text = text.replace(i, " " + i)
            
    return text
'''

def create_data(df, filepath):
    '''
    The function responsible for the creation of data in the said format.
    '''
    with open(filepath , 'w') as f:
        for text, annotation in zip(df.text, df.annotation):
            #text = clean(text) # Cleaning need to be done in preprocessing
            text_ = text        
            match_list = []
            for i in annotation:
                a, text_ = matcher(text, i[0])
                match_list.append((a[0][0], a[0][1], i[1]))

            d = mark_sentence(text, match_list)

            for i in d.keys():
                f.writelines(i + ' ' + d[i] +'\n')
            f.writelines('\n')
            



In [20]:
## Subset and rename Train
bio_df = df[["text", "labels"]].copy()
bio_df.rename(columns = {'text':'text', 'labels':'annotation'}, inplace = True)


In [21]:
#Create and Store NER task file
full_filepath = 'data/bio_drugs_corpusV1.2.txt'
create_data(bio_df, full_filepath)

In [22]:
bio_df.shape

(38174, 2)

In [23]:
bio_train, bio_test = train_test_split(bio_df, test_size=0.1, random_state=42, shuffle=True)#10% --> 3900 rows should be enough
bio_train, bio_dev = train_test_split(bio_train, test_size=0.1, random_state=42, shuffle=True)

train_filepath = 'data/bio_drugs_corpus_trainV1.2.txt'
dev_filepath = 'data/bio_drugs_corpus_devV1.2.txt'
test_filepath = 'data/bio_drugs_corpus_testV1.2.txt'

create_data(bio_train, train_filepath)
create_data(bio_dev, dev_filepath)
create_data(bio_test, test_filepath)
